In [1]:
import pandas as pd
import numpy as np

# -------------------------------------------------------------------
# 1. Ruta del archivo Excel
# -------------------------------------------------------------------
excel_path = r"C:\Users\julio\OneDrive\Documentos\Trabajo\Ideas Frescas\Proyectos\REM\BD\BD_Mazatlan.xlsm" # AJUSTA ESTA RUTA SI ES NECESARIO

# -------------------------------------------------------------------
# 2. Cargar hojas necesarias
# -------------------------------------------------------------------
vertical   = pd.read_excel(excel_path, sheet_name="Vertical")
horizontal = pd.read_excel(excel_path, sheet_name="Horizontal")
lote       = pd.read_excel(excel_path, sheet_name="Lote")

ventas   = pd.read_excel(excel_path, sheet_name="Ventas")
precios  = pd.read_excel(excel_path, sheet_name="Precios")
info_v   = pd.read_excel(excel_path, sheet_name="Info_Prototipos_vertical")
info_h   = pd.read_excel(excel_path, sheet_name="Info_Prototipos_horizontal")
info_l   = pd.read_excel(excel_path, sheet_name="Info_Prototipos_lote")

# NOTA: rep_prot ya no se usa, lo quitamos
# rep_prot = pd.read_excel(excel_path, sheet_name="Reporte_Prototipos")

# Fecha más reciente global en la hoja de Precios
ultima_fecha_precios = precios["Fecha"].max()

# -------------------------------------------------------------------
# 3. Helpers básicos
# -------------------------------------------------------------------
def build_tipo_map():
    """
    Mapa: Nombre_desarrollo -> tipo de proyecto (vertical / horizontal / lote)
    """
    m = {}
    for tipo, df in [("vertical", vertical),
                     ("horizontal", horizontal),
                     ("lote", lote)]:
        for dev in df["Nombre_desarrollo"].dropna().unique():
            if dev not in m:
                m[dev] = tipo
    return m

tipo_map = build_tipo_map()

def proyectos_disponibles(df):
    """
    Devuelve el set de desarrollos con Estatus_venta = 'Disponible'
    en una hoja (Vertical / Horizontal / Lote).
    """
    return set(
        df.loc[
            df["Estatus_venta"].astype(str).str.lower().eq("disponible"),
            "Nombre_desarrollo"
        ].dropna()
    )

# -------------------------------------------------------
# Proyectos objetivo
# -------------------------------------------------------

# A) Proyectos disponibles
proy_disp = (
    proyectos_disponibles(vertical)
    | proyectos_disponibles(horizontal)
    | proyectos_disponibles(lote)
)

# Obtener última fecha global en la hoja Ventas
ultima_fecha_ventas = ventas["Fecha"].max()

def proyectos_vendidos_ultimo_periodo(df):
    """
    Devuelve los proyectos con:
    - Estatus_venta = 'Vendido'
    - Fecha_fin_ventas = última fecha del periodo (de hoja Ventas)
    """
    mask = (
        df["Estatus_venta"].astype(str).str.lower().eq("vendido")
        & (pd.to_datetime(df["Fecha_fin_ventas"]) == ultima_fecha_ventas)
    )
    return set(df.loc[mask, "Nombre_desarrollo"].dropna())

proy_vendidos_v = proyectos_vendidos_ultimo_periodo(vertical)
proy_vendidos_h = proyectos_vendidos_ultimo_periodo(horizontal)
proy_vendidos_l = proyectos_vendidos_ultimo_periodo(lote)

proy_vendidos_ult = proy_vendidos_v | proy_vendidos_h | proy_vendidos_l

# CONJUNTO FINAL
proyectos_objetivo = sorted(proy_disp | proy_vendidos_ult)

# -------------------------------------------------------------------
# 4. Información base por desarrollo (tipo, desarrollador, zona, etc.)
# -------------------------------------------------------------------
def get_base_info(desarrollo):
    tipo = tipo_map.get(desarrollo)

    if tipo == "vertical":
        df = vertical
        col_total = "Departamentos_planeados"
    elif tipo == "horizontal":
        df = horizontal
        col_total = "Casas_planeados"
    elif tipo == "lote":
        df = lote
        col_total = "Lotes_planeados"
    else:
        return {}

    row = df[df["Nombre_desarrollo"] == desarrollo].iloc[0]

    return {
        "Tipo de proyecto"       : tipo,
        "Desarrollador"          : row.get("Desarrolladora", np.nan),
        "Comercializadora"       : row.get("Comercializadora", np.nan),
        "Zona"                   : row.get("Zona", np.nan),
        "# meses en venta"       : row.get("Meses_venta", np.nan),
        "Oferta total"           : row.get(col_total, np.nan),
        "Fecha_inicio_venta"     : row.get("Fecha_inicio_venta", np.nan),
    }


# -------------------------------------------------------------------
# 5. Métricas de ventas (históricas y mensuales)
# -------------------------------------------------------------------
def get_ventas_metrics(desarrollo, meses_venta, fecha_inicio_venta):
    """
    Calcula:
    - Ventas mensuales históricas
    - Ventas mensuales (con validación de proyectos recién metidos)
    - Oferta disponible anterior / actual
    - Oferta vendida
    """
    dfv = ventas[ventas["Nombre_desarrollo"] == desarrollo].sort_values("Fecha")

    if dfv.empty:
        return {
            "Ventas mensuales históricas" : np.nan,
            "Ventas mensuales"            : np.nan,
            "Oferta disponible anterior"  : np.nan,
            "Oferta disponible actual"    : np.nan,
            "Oferta vendida"              : np.nan,
        }

    last = dfv.iloc[-1]

    # Ventas mensuales históricas = Ventas_acumuladas último registro / Meses_venta
    if pd.notna(meses_venta) and meses_venta not in (0, 0.0):
        v_hist = last.get("Ventas_acumuladas", np.nan) / meses_venta
    else:
        v_hist = np.nan

    # Inicializamos valores por defecto
    v_mensual   = np.nan
    oferta_ant  = np.nan

    # Convertimos fechas a Timestamp
    last_date = pd.to_datetime(last["Fecha"])

    fecha_ini = pd.to_datetime(fecha_inicio_venta) if pd.notna(fecha_inicio_venta) else None

    # -------- CASO 1: SOLO UN REGISTRO EN VENTAS PARA ESE PROYECTO --------
    if len(dfv) == 1:

        if fecha_ini is not None:
            mismo_mes_anyo = (fecha_ini.year == last_date.year) and (fecha_ini.month == last_date.month)

            if mismo_mes_anyo:
                # Proyecto que inicia preventa justo en el último periodo:
                # Ventas mensuales = Ventas_acumuladas (primer mes completo)
                v_mensual = last.get("Ventas_acumuladas", np.nan)
            else:
                # Proyecto ya venía de antes pero solo se cargó en este corte:
                # Ventas mensuales = Ventas mensuales históricas
                v_mensual = v_hist
        else:
            # Sin fecha de inicio, usamos la histórica
            v_mensual = v_hist

    # -------- CASO 2: DOS O MÁS REGISTROS EN VENTAS --------
    else:
        prev = dfv.iloc[-2]
        d1 = last_date
        d0 = pd.to_datetime(prev["Fecha"])
        diff_meses = (d1.year - d0.year) * 12 + (d1.month - d0.month)

        if diff_meses > 0:
            v_mensual = last.get("Ventas_periodo", np.nan) / diff_meses
        else:
            v_mensual = np.nan

        oferta_ant = prev.get("Inventario_disponible", np.nan)

    return {
        "Ventas mensuales históricas" : v_hist,
        "Ventas mensuales"            : v_mensual,
        "Oferta disponible anterior"  : oferta_ant,
        "Oferta disponible actual"    : last.get("Inventario_disponible", np.nan),
        "Oferta vendida"              : last.get("Ventas_acumuladas", np.nan),
    }

# -------------------------------------------------------------------
# 6. Prototipo +ven, precios y tamaños (m2)
# -------------------------------------------------------------------
def get_info_df_by_tipo(tipo):
    if tipo == "vertical":
        return info_v
    if tipo == "horizontal":
        return info_h
    if tipo == "lote":
        return info_l
    return None

def get_prototipo_y_precios(desarrollo, tipo):
    """
    Calcula a partir SOLO de la fecha más reciente (ultima_fecha_precios):
    - +ven (precio del prototipo más vendido o, si no está marcado, el de menor precio > 0)
    - Precio mínimo / máximo en el último periodo
    - Tamaño prom. terreno m2 (según tipo)
    - Tamaño prom. constr. m2 (según tipo)
    - Precio prom. m2 terreno
    - Precio prom. m2 constr.
    """
    # Filtrar filas de ese desarrollo
    df_pre_dev = precios[precios["Nombre_desarrollo"] == desarrollo]

    # Resultado inicial
    resultado = {
        "  +ven"                    : np.nan,
        "Precio mínimo"            : np.nan,
        "Precio máximo"            : np.nan,
        "Tamaño prom. terreno m2"  : 0.0 if tipo != "vertical" else np.nan,
        "Tamaño prom. constr. m2"  : 0.0 if tipo != "lote" else np.nan,
        "Precio prom. m2 terreno"  : np.nan,
        "Precio prom. m2 constr."  : np.nan,
    }

    # Si no hay ningún registro para ese desarrollo, regresamos NaN
    if df_pre_dev.empty:
        return resultado

    # Tomar SOLO la fecha más reciente GLOBAL
    df_last = df_pre_dev[df_pre_dev["Fecha"] == ultima_fecha_precios]

    # Si ese desarrollo no tiene datos en la fecha más reciente, regresamos NaN
    if df_last.empty:
        return resultado

    # Precio mínimo y máximo (último periodo global, excluyendo 0)
    precios_validos = df_last["Precio"].dropna()
    precios_validos = precios_validos[precios_validos > 0]

    if not precios_validos.empty:
        resultado["Precio mínimo"] = precios_validos.min()
        resultado["Precio máximo"] = precios_validos.max()

    # -------------------------------------------------------------------
    # Selección del prototipo más vendido (“+ ven”) SOLO de la fecha más reciente
    # -------------------------------------------------------------------
    prototipo = None
    price_ven = np.nan

    if  "  +ven" in df_last.columns:
        col = df_last[ "  +ven"]

        # Construimos un mask de "verdaderos" robusto (bool o texto)
        if col.dtype == bool:
            mask_true = col
        else:
            col_str = col.astype(str).str.strip().str.upper()
            mask_true = col_str.isin(["VERDADERO", "TRUE", "SÍ", "SI", "1", "YES"])

        protos_marcados = df_last[mask_true]

        if not protos_marcados.empty:
            row_flag = protos_marcados.iloc[0]
            prototipo = row_flag["Nombre_prototipos"]
            price_ven = row_flag["Precio"]

    # 2) Si NO hubo marcado → prototipo de MENOR precio != 0 de esa MISMA fecha
    if prototipo is None or pd.isna(price_ven) or price_ven == 0:
        df_valid_price = df_last[df_last["Precio"] > 0]
        if not df_valid_price.empty:
            row_min = df_valid_price.loc[df_valid_price["Precio"].idxmin()]
            prototipo = row_min["Nombre_prototipos"]
            price_ven = row_min["Precio"]

    resultado[ "  +ven"] = price_ven

    # Tamaños m2 desde Info_Prototipos_*
    info_df = get_info_df_by_tipo(tipo)
    if info_df is not None and prototipo is not None:
        info_row = info_df[
            (info_df["Nombre_desarrollo"] == desarrollo)
            & (info_df["Nombre_prototipos"] == prototipo)
        ]
        if not info_row.empty:
            info_row = info_row.iloc[0]

            # Terreno
            if tipo in ("horizontal", "lote"):
                resultado["Tamaño prom. terreno m2"] = info_row.get("Medida_terreno", np.nan)

            # Construcción
            if tipo in ("vertical", "horizontal"):
                resultado["Tamaño prom. constr. m2"] = info_row.get("Medida_construcción", np.nan)

    # Precios por m2
    terr = resultado["Tamaño prom. terreno m2"]
    cons = resultado["Tamaño prom. constr. m2"]

    if pd.notna(resultado[ "  +ven"]) and isinstance(resultado[ "  +ven"], (int, float, np.floating)):
        price_ven = float(resultado[ "  +ven"])

        if tipo != "vertical" and pd.notna(terr) and terr not in (0, 0.0):
            resultado["Precio prom. m2 terreno"] = price_ven / terr

        if tipo != "lote" and pd.notna(cons) and cons not in (0, 0.0):
            resultado["Precio prom. m2 constr."] = price_ven / cons

    return resultado


# -------------------------------------------------------------------
# 7. Construir el DataFrame final
# -------------------------------------------------------------------
filas = []

for dev in proyectos_objetivo:
    base   = get_base_info(dev)
    tipo   = base["Tipo de proyecto"]

    ventas_metrics   = get_ventas_metrics(
        desarrollo=dev,
        meses_venta=base["# meses en venta"],
        fecha_inicio_venta=base["Fecha_inicio_venta"]
    )

    precios_metrics  = get_prototipo_y_precios(dev, tipo)

    oferta_total   = base["Oferta total"]
    oferta_vendida = ventas_metrics["Oferta vendida"]

    # % vendido = Oferta vendida / Oferta total
    if pd.notna(oferta_total) and oferta_total not in (0, 0.0) and pd.notna(oferta_vendida):
        pct_vendido = oferta_vendida / oferta_total
    else:
        pct_vendido = np.nan

    fila = {
        "Desarrollo"                 : dev,
        "Desarrollador"              : base["Desarrollador"],
        "Comercializadora"           : base["Comercializadora"],
        "  +ven"                     : precios_metrics["  +ven"],
        "Precio mínimo"              : precios_metrics["Precio mínimo"],
        "Precio máximo"              : precios_metrics["Precio máximo"],
        "Ventas mensuales históricas": ventas_metrics["Ventas mensuales históricas"],
        "Ventas mensuales"           : ventas_metrics["Ventas mensuales"],
        "# meses en venta"           : base["# meses en venta"],
        "Oferta disponible anterior" : ventas_metrics["Oferta disponible anterior"],
        "Oferta disponible actual"   : ventas_metrics["Oferta disponible actual"],
        "Oferta vendida"             : oferta_vendida,
        "Oferta total"               : oferta_total,
        "% vendido"                  : pct_vendido,
        "Tamaño prom. terreno m2"    : precios_metrics["Tamaño prom. terreno m2"],
        "Tamaño prom. constr. m2"    : precios_metrics["Tamaño prom. constr. m2"],
        "Precio prom. m2 terreno"    : precios_metrics["Precio prom. m2 terreno"],
        "Precio prom. m2 constr."    : precios_metrics["Precio prom. m2 constr."],
        "Tipo de proyecto"           : base["Tipo de proyecto"],
        "Zona"                       : base["Zona"],
    }

    filas.append(fila)

df_resumen = pd.DataFrame(filas)
df_resumen['Tipo de proyecto'] = df_resumen['Tipo de proyecto'].str.capitalize()

# -------------------------------------------------------------------
# 8. Guardar a CSV
# -------------------------------------------------------------------
output_csv = "Resumen_Disponibles_1_linea.csv"
df_resumen.to_csv(output_csv, index=False, encoding="utf-8-sig")

print(f"Archivo generado: {output_csv}")
df_resumen.head(10)


Archivo generado: Resumen_Disponibles_1_linea.csv


Desarrollo          Desarrollador  \
0                                     5th Level                Privado   
1                                         Adora                 Lafher   
2  Aguamarina Talismán- Torre Aqua Vista Ciudad                 Vicasa   
3  Aguamarina Talismán- Torre Azul Vista al Mar                 Vicasa   
4                                 Aitana Condos  Turquezas Desarrollos   
5                        Akkúun Marina Mazatlán                Privado   
6                                         Akoya               Lizantos   
7                                  Aldea Ananta                    TDL   
8                             Alicante (El Cid)   El Cid Bienes Raíces   
9                  Altazia Residencial- Etapa 5                Privado   

                Comercializadora    +ven  Precio mínimo  Precio máximo  \
0                        Regency     NaN            NaN            NaN   
1                        Lafher      NaN            NaN            NaN   
2                            NaN     NaN            NaN            NaN   
3                            NaN     NaN            NaN            NaN   
4          Turquezas Desarrollos     NaN            NaN            NaN   
5   Depreventa, Sol Inmobiliaria     NaN            NaN            NaN   
6                       Lizantos     NaN            NaN            NaN   
7  Regency, Sol Inmobiliaria, KW     NaN            NaN            NaN   
8                            NaN     NaN            NaN            NaN   
9                            NaN     NaN            NaN            NaN   

   Ventas mensuales históricas  Ventas mensuales  # meses en venta  \
0                     0.333333          0.333333              27.0   
1                     1.812500          0.666667              32.0   
2                     1.133333          0.000000              45.0   
3                     7.644444          0.000000              45.0   
4                     1.423077          1.333333              26.0   
5                     2.069767          1.666667              43.0   
6                     1.326531          0.000000              49.0   
7                     1.450980          0.666667              51.0   
8                     0.593220          0.000000              59.0   
9                     4.212121          2.000000              33.0   

   Oferta disponible anterior  Oferta disponible actual  Oferta vendida  \
0                        16.0                      15.0             9.0   
1                        20.0                      18.0            58.0   
2                        25.0                      25.0            51.0   
3                        28.0                      41.0           344.0   
4                        30.0                      26.0            37.0   
5                        27.0                      22.0            89.0   
6                         7.0                      10.0            65.0   
7                         3.0                       1.0            74.0   
8                        10.0                      10.0            35.0   
9                        72.0                      66.0           139.0   

   Oferta total  % vendido  Tamaño prom. terreno m2  Tamaño prom. constr. m2  \
0          24.0   0.375000                      NaN                      0.0   
1          76.0   0.763158                      NaN                      0.0   
2          76.0   0.671053                      NaN                      0.0   
3         385.0   0.893506                      NaN                      0.0   
4          63.0   0.587302                      NaN                      0.0   
5         111.0   0.801802                      NaN                      0.0   
6          75.0   0.866667                      NaN                      0.0   
7          75.0   0.986667                      NaN                      0.0   
8          45.0   0.777778                      0.0                      NaN   
9         

In [ ]:
import pandas as pd
import numpy as np

# -------------------------------------------------------------------
# 1. Ruta del archivo Excel
# -------------------------------------------------------------------
excel_path = r"C:\Users\julio\OneDrive\Documentos\Trabajo\Ideas Frescas\Proyectos\REM\BD\BD_Mazatlan.xlsm"
# -------------------------------------------------------------------
# 2. Cargar hojas necesarias
# -------------------------------------------------------------------
vertical   = pd.read_excel(excel_path, sheet_name="Vertical")
horizontal = pd.read_excel(excel_path, sheet_name="Horizontal")
lote       = pd.read_excel(excel_path, sheet_name="Lote")

ventas   = pd.read_excel(excel_path, sheet_name="Ventas")
precios  = pd.read_excel(excel_path, sheet_name="Precios")
info_v   = pd.read_excel(excel_path, sheet_name="Info_Prototipos_vertical")
info_h   = pd.read_excel(excel_path, sheet_name="Info_Prototipos_horizontal")
info_l   = pd.read_excel(excel_path, sheet_name="Info_Prototipos_lote")

# Fecha más reciente global en PRECIOS
ultima_fecha_precios = precios["Fecha"].max()


# -------------------------------------------------------------------
# 3. Helper para saber tipo de proyecto
# -------------------------------------------------------------------
def build_tipo_map():
    m = {}
    for tipo, df in [("vertical", vertical),
                     ("horizontal", horizontal),
                     ("lote", lote)]:
        for dev in df["Nombre_desarrollo"].dropna().unique():
            m[dev] = tipo
    return m

tipo_map = build_tipo_map()


# -------------------------------------------------------------------
# 4. Helpers de prototipos
# -------------------------------------------------------------------
def get_info_df(tipo):
    if tipo == "vertical": return info_v
    if tipo == "horizontal": return info_h
    if tipo == "lote": return info_l


def get_prototipo_info_correcta(df_p):
    """
    Aplica las VALIDACIONES:
    1. Si hay un "+ ven = VERDADERO" usar ese prototipo.
    2. Si NO hay marcado -> tomar el precio mínimo > 0 del último periodo.
    """

    # Filtramos solo precios > 0
    df_valid = df_p[df_p["Precio"] > 0]

    # 1. Buscar prototipo marcado " + ven"
    if " + ven" in df_p.columns:

        col = df_p[" + ven"]

        # Normalizar valores VERDADERO/TRUE/SI
        col_str = col.astype(str).str.strip().str.upper()
        mask_true = col_str.isin(["VERDADERO", "TRUE", "SÍ", "SI", "1", "YES"])

        df_marked = df_p[mask_true]

        if not df_marked.empty:
            row = df_marked.iloc[0]
            return row["Nombre_prototipos"], row["Precio"]

    # 2. Si NO hay marcado → prototipo con precio más bajo > 0
    if not df_valid.empty:
        row_min = df_valid.loc[df_valid["Precio"].idxmin()]
        return row_min["Nombre_prototipos"], row_min["Precio"]

    return None, np.nan


# -------------------------------------------------------------------
# 5. VENTAS (con validación de proyectos nuevos)
# -------------------------------------------------------------------
def get_ventas_metrics_3(proyecto, meses_venta):

    dfv = ventas[ventas["Nombre_desarrollo"] == proyecto].sort_values("Fecha")
    if dfv.empty:
        return np.nan, np.nan, 0, 0, 0

    last = dfv.iloc[-1]

    # Histórica
    v_hist = last["Ventas_acumuladas"] / meses_venta if meses_venta not in (0, np.nan) else np.nan

    # Ventas mensuales
    if len(dfv) >= 2:
        prev = dfv.iloc[-2]
        diff = (pd.to_datetime(last["Fecha"]).year - pd.to_datetime(prev["Fecha"]).year) * 12 + \
               (pd.to_datetime(last["Fecha"]).month - pd.to_datetime(prev["Fecha"]).month)
        v_mensual = last["Ventas_periodo"] / diff if diff > 0 else v_hist
        oferta_ant = prev["Inventario_disponible"]
    else:
        v_mensual = v_hist
        oferta_ant = 0

    oferta_act = last["Inventario_disponible"]
    oferta_vendida = last["Ventas_acumuladas"]

    return v_hist, v_mensual, oferta_ant, oferta_act, oferta_vendida


# -------------------------------------------------------------------
# 6. GENERAR TABLA DE 3 LÍNEAS ( +vend, Min, Max )
# -------------------------------------------------------------------
rows = []

# Usar solo los proyectos OBJETIVO (como resumen 1 línea)
# -----------------------------------
# Para esto reutilizamos tus criterios:
def proyectos_disponibles(df):
    return set(
        df.loc[df["Estatus_venta"].astype(str).str.lower().eq("disponible"),
               "Nombre_desarrollo"].dropna()
    )

proy_disp = proyectos_disponibles(vertical) \
          | proyectos_disponibles(horizontal) \
          | proyectos_disponibles(lote)

ultima_fecha_ventas = ventas["Fecha"].max()

def proyectos_vendidos_ultimo_periodo(df):
    mask = (
        df["Estatus_venta"].astype(str).str.lower().eq("vendido")
        & (pd.to_datetime(df["Fecha_fin_ventas"]) == ultima_fecha_ventas)
    )
    return set(df.loc[mask, "Nombre_desarrollo"].dropna())

proy_vendidos = proyectos_vendidos_ultimo_periodo(vertical) \
              | proyectos_vendidos_ultimo_periodo(horizontal) \
              | proyectos_vendidos_ultimo_periodo(lote)

proyectos_objetivo = sorted(proy_disp | proy_vendidos)


# -------------------------------------------------------------------
# LOOP PRINCIPAL
# -------------------------------------------------------------------
for proyecto in proyectos_objetivo:

    tipo = tipo_map.get(proyecto)
    if tipo is None:
        continue

    # Datos base
    if tipo == "vertical":
        df_info = vertical
        col_total = "Departamentos_planeados"
    elif tipo == "horizontal":
        df_info = horizontal
        col_total = "Casas_planeados"
    else:
        df_info = lote
        col_total = "Lotes_planeados"

    base = df_info[df_info["Nombre_desarrollo"] == proyecto].iloc[0]

    desarrollador = base.get("Desarrolladora", np.nan)
    zona          = base.get("Zona", np.nan)
    enganche      = base.get("%_enganche", np.nan)
    meses_venta   = base.get("Meses_venta", np.nan)
    oferta_total  = base.get(col_total, np.nan)

    # -------------------------------------------------------------------
    # PRECIOS DEL ÚLTIMO PERIODO GLOBAL
    # -------------------------------------------------------------------
    df_p = precios[(precios["Nombre_desarrollo"] == proyecto) &
                   (precios["Fecha"] == ultima_fecha_precios)]

    if df_p.empty:
        continue

    df_valid = df_p[df_p["Precio"] > 0]
    if df_valid.empty:
        continue

    # Prototipos con reglas correctas
    prot_ven, precio_ven = get_prototipo_info_correcta(df_p)

    prot_min = df_valid.loc[df_valid["Precio"].idxmin(), "Nombre_prototipos"]
    precio_min = df_valid["Precio"].min()

    prot_max = df_valid.loc[df_valid["Precio"].idxmax(), "Nombre_prototipos"]
    precio_max = df_valid["Precio"].max()

    # -------------------------------------------------------------------
    # TAMAÑOS (m2)
    # -------------------------------------------------------------------
    info_df = get_info_df(tipo)

    def get_m2(des, prot):
        row = info_df[(info_df["Nombre_desarrollo"] == des) &
                       (info_df["Nombre_prototipos"] == prot)]
        if row.empty:
            return np.nan
        row = row.iloc[0]
        if tipo == "lote":
            return row.get("Medida_terreno", np.nan)
        return row.get("Medida_construcción", np.nan)

    m2_ven = get_m2(proyecto, prot_ven)
    m2_min = get_m2(proyecto, prot_min)
    m2_max = get_m2(proyecto, prot_max)

    # -------------------------------------------------------------------
    # VENTAS
    # -------------------------------------------------------------------
    v_hist, v_mensual, oferta_ant, oferta_act, oferta_vendida = \
        get_ventas_metrics_3(proyecto, meses_venta)

    pct_vend = oferta_vendida / oferta_total if oferta_total not in (0, np.nan) else np.nan

    # -------------------------------------------------------------------
    # ESTIMACIÓN
    # -------------------------------------------------------------------
    v_est = v_mensual if v_mensual > 0 else v_hist
    estimacion = oferta_act / v_est if v_est not in (0, np.nan) else np.nan

    # -------------------------------------------------------------------
    # FUNCIÓN PARA AGREGAR FILAS
    # -------------------------------------------------------------------
    def add_row(criterio, prot, precio, m2):
        rows.append({
            "Desarrollo"                 : proyecto,
            "Desarrollador"              : desarrollador,
            "Criterios"                  : criterio,
            "Constr."                    : m2,
            "Precio final"               : precio,
            "Precio x m2"                : precio / m2 if m2 not in (0, np.nan) else np.nan,
            "Ventas mensuales históricas": v_hist,
            "Ventas mensuales"           : v_mensual,
            "Oferta disponible anterior" : oferta_ant,
            "Oferta disponible actual"   : oferta_act,
            "Oferta vendida"             : oferta_vendida,
            "Oferta total"               : oferta_total,
            "% vendido"                  : pct_vend,
            "# de meses en venta"        : meses_venta,
            "Estimación"                 : estimacion,
            "Enganche"                   : enganche,
            "Tipo de proyecto"           : tipo,
            "Zona"                       : zona
        })

    # -------------------------------------------------------------------
    # AGREGAR LAS TRES LÍNEAS
    # -------------------------------------------------------------------
    add_row( "  +ven", prot_ven, precio_ven, m2_ven)
    add_row("Min",    prot_min, precio_min, m2_min)
    add_row("Max",    prot_max, precio_max, m2_max)


# -------------------------------------------------------------------
# 7. Guardar CSV
# -------------------------------------------------------------------
df_3lineas = pd.DataFrame(rows)
df_3lineas['Tipo de proyecto'] = df_3lineas['Tipo de proyecto'].str.capitalize()
df_3lineas.to_csv("Resumen_Disponibles_3_lineas.csv", index=False, encoding="utf-8-sig")

print("Archivo generado: Resumen_Disponibles_3_lineas.csv")
df_3lineas.head(20)


In [4]:
import pandas as pd
import numpy as np

# -------------------------------------------------------------------
# 1. Ruta del archivo Excel
# -------------------------------------------------------------------
excel_path = r"C:\Users\julio\OneDrive\Documentos\Trabajo\Ideas Frescas\Proyectos\REM\BD\BD_Mazatlan.xlsm"

# -------------------------------------------------------------------
# 2. Cargar hojas necesarias
# -------------------------------------------------------------------
vertical   = pd.read_excel(excel_path, sheet_name="Vertical")
horizontal = pd.read_excel(excel_path, sheet_name="Horizontal")
lote       = pd.read_excel(excel_path, sheet_name="Lote")

ventas   = pd.read_excel(excel_path, sheet_name="Ventas")
precios  = pd.read_excel(excel_path, sheet_name="Precios")
info_v   = pd.read_excel(excel_path, sheet_name="Info_Prototipos_vertical")
info_h   = pd.read_excel(excel_path, sheet_name="Info_Prototipos_horizontal")
info_l   = pd.read_excel(excel_path, sheet_name="Info_Prototipos_lote")

# Fechas más recientes
ultima_fecha_precios = precios["Fecha"].max()
ultima_fecha_ventas  = ventas["Fecha"].max()

# -------------------------------------------------------------------
# 3. Helpers de Mapas y Tipos
# -------------------------------------------------------------------
def build_tipo_map():
    m = {}
    for tipo, df in [("vertical", vertical), ("horizontal", horizontal), ("lote", lote)]:
        for dev in df["Nombre_desarrollo"].dropna().unique():
            if dev not in m:
                m[dev] = tipo
    return m

tipo_map = build_tipo_map()

def get_info_df(tipo):
    if tipo == "vertical": return info_v
    if tipo == "horizontal": return info_h
    if tipo == "lote": return info_l

# -------------------------------------------------------------------
# 4. [REUSADO DEL CODIGO 1] Información Base
# -------------------------------------------------------------------
def get_base_info(desarrollo):
    tipo = tipo_map.get(desarrollo)

    if tipo == "vertical":
        df = vertical
        col_total = "Departamentos_planeados"
    elif tipo == "horizontal":
        df = horizontal
        col_total = "Casas_planeados"
    elif tipo == "lote":
        df = lote
        col_total = "Lotes_planeados"
    else:
        return {}

    # Filtrar con seguridad
    rows = df[df["Nombre_desarrollo"] == desarrollo]
    if rows.empty:
        return {}
    
    row = rows.iloc[0]

    return {
        "Tipo de proyecto"       : tipo,
        "Desarrollador"          : row.get("Desarrolladora", np.nan),
        "Comercializadora"       : row.get("Comercializadora", np.nan),
        "Zona"                   : row.get("Zona", np.nan),
        "# meses en venta"       : row.get("Meses_venta", np.nan),
        "Oferta total"           : row.get(col_total, np.nan),
        "Fecha_inicio_venta"     : row.get("Fecha_inicio_venta", np.nan),
        "Enganche"               : row.get("%_enganche", np.nan) # Agregado para Codigo 2
    }

# -------------------------------------------------------------------
# 5. [REUSADO DEL CODIGO 1] Métricas de Ventas Robustas
# -------------------------------------------------------------------
def get_ventas_metrics(desarrollo, meses_venta, fecha_inicio_venta):
    """
    Calcula ventas mensuales validando si es lanzamiento reciente o histórico.
    """
    dfv = ventas[ventas["Nombre_desarrollo"] == desarrollo].sort_values("Fecha")

    if dfv.empty:
        return {
            "Ventas mensuales históricas" : np.nan,
            "Ventas mensuales"            : np.nan,
            "Oferta disponible anterior"  : np.nan,
            "Oferta disponible actual"    : np.nan,
            "Oferta vendida"              : np.nan,
        }

    last = dfv.iloc[-1]

    # Históricas
    if pd.notna(meses_venta) and meses_venta not in (0, 0.0):
        v_hist = last.get("Ventas_acumuladas", np.nan) / meses_venta
    else:
        v_hist = np.nan

    v_mensual = np.nan
    oferta_ant = np.nan
    last_date = pd.to_datetime(last["Fecha"])
    fecha_ini = pd.to_datetime(fecha_inicio_venta) if pd.notna(fecha_inicio_venta) else None

    # CASO 1: UN SOLO REGISTRO
    if len(dfv) == 1:
        if fecha_ini is not None:
            mismo_mes_anyo = (fecha_ini.year == last_date.year) and (fecha_ini.month == last_date.month)
            if mismo_mes_anyo:
                v_mensual = last.get("Ventas_acumuladas", np.nan) # Es lanzamiento real
            else:
                v_mensual = v_hist # Es carga antigua
        else:
            v_mensual = v_hist

    # CASO 2: MÚLTIPLES REGISTROS
    else:
        prev = dfv.iloc[-2]
        d1 = last_date
        d0 = pd.to_datetime(prev["Fecha"])
        diff_meses = (d1.year - d0.year) * 12 + (d1.month - d0.month)

        if diff_meses > 0:
            v_mensual = last.get("Ventas_periodo", np.nan) / diff_meses
        else:
            v_mensual = np.nan
        
        oferta_ant = prev.get("Inventario_disponible", np.nan)

    return {
        "Ventas mensuales históricas" : v_hist,
        "Ventas mensuales"            : v_mensual,
        "Oferta disponible anterior"  : oferta_ant,
        "Oferta disponible actual"    : last.get("Inventario_disponible", np.nan),
        "Oferta vendida"              : last.get("Ventas_acumuladas", np.nan),
    }

# -------------------------------------------------------------------
# 6. Helper Prototipos (Lógica específica de 3 líneas)
# -------------------------------------------------------------------
def get_prototipo_info_correcta(df_p):
    # Filtramos precios > 0
    df_valid = df_p[df_p["Precio"] > 0]

    # 1. Buscar marcado " + ven"
    if " + ven" in df_p.columns:
        col = df_p[" + ven"]
        col_str = col.astype(str).str.strip().str.upper()
        mask_true = col_str.isin(["VERDADERO", "TRUE", "SÍ", "SI", "1", "YES"])
        df_marked = df_p[mask_true]

        if not df_marked.empty:
            row = df_marked.iloc[0]
            return row["Nombre_prototipos"], row["Precio"]

    # 2. Si no, el menor precio
    if not df_valid.empty:
        row_min = df_valid.loc[df_valid["Precio"].idxmin()]
        return row_min["Nombre_prototipos"], row_min["Precio"]

    return None, np.nan

# -------------------------------------------------------------------
# 7. Selección de Proyectos Objetivo (Igual que Codigo 1)
# -------------------------------------------------------------------
def proyectos_disponibles(df):
    return set(df.loc[df["Estatus_venta"].astype(str).str.lower().eq("disponible"), "Nombre_desarrollo"].dropna())

def proyectos_vendidos_ultimo_periodo(df):
    mask = (df["Estatus_venta"].astype(str).str.lower().eq("vendido") & 
            (pd.to_datetime(df["Fecha_fin_ventas"]) == ultima_fecha_ventas))
    return set(df.loc[mask, "Nombre_desarrollo"].dropna())

proy_disp = proyectos_disponibles(vertical) | proyectos_disponibles(horizontal) | proyectos_disponibles(lote)
proy_vendidos = proyectos_vendidos_ultimo_periodo(vertical) | proyectos_vendidos_ultimo_periodo(horizontal) | proyectos_vendidos_ultimo_periodo(lote)

proyectos_objetivo = sorted(proy_disp | proy_vendidos)

# -------------------------------------------------------------------
# 8. LOOP PRINCIPAL (3 Líneas)
# -------------------------------------------------------------------
rows = []

for proyecto in proyectos_objetivo:
    
    # 1. Usar get_base_info (Mejora del Codigo 1)
    base = get_base_info(proyecto)
    if not base: continue # Si devolvió dict vacío

    tipo = base["Tipo de proyecto"]
    desarrollador = base["Desarrollador"]
    zona = base["Zona"]
    enganche = base["Enganche"]
    meses_venta = base["# meses en venta"]
    oferta_total = base["Oferta total"]
    fecha_ini = base["Fecha_inicio_venta"]

    # 2. Precios
    df_p = precios[(precios["Nombre_desarrollo"] == proyecto) & (precios["Fecha"] == ultima_fecha_precios)]
    if df_p.empty: continue

    df_valid = df_p[df_p["Precio"] > 0]
    if df_valid.empty: continue

    # Datos para las 3 líneas
    prot_ven, precio_ven = get_prototipo_info_correcta(df_p)
    
    prot_min = df_valid.loc[df_valid["Precio"].idxmin(), "Nombre_prototipos"]
    precio_min = df_valid["Precio"].min()
    
    prot_max = df_valid.loc[df_valid["Precio"].idxmax(), "Nombre_prototipos"]
    precio_max = df_valid["Precio"].max()

    # 3. Tamaños (m2)
    info_df = get_info_df(tipo)

    def get_m2(des, prot):
        if info_df is None: return np.nan
        row = info_df[(info_df["Nombre_desarrollo"] == des) & (info_df["Nombre_prototipos"] == prot)]
        if row.empty: return np.nan
        row = row.iloc[0]
        if tipo == "lote": return row.get("Medida_terreno", np.nan)
        return row.get("Medida_construcción", np.nan)

    m2_ven = get_m2(proyecto, prot_ven)
    m2_min = get_m2(proyecto, prot_min)
    m2_max = get_m2(proyecto, prot_max)

    # 4. VENTAS (Usando la función robusta del Codigo 1)
    metrics = get_ventas_metrics(proyecto, meses_venta, fecha_ini)
    
    v_hist = metrics["Ventas mensuales históricas"]
    v_mensual = metrics["Ventas mensuales"]
    oferta_ant = metrics["Oferta disponible anterior"]
    oferta_act = metrics["Oferta disponible actual"]
    oferta_vendida = metrics["Oferta vendida"]

    # Cálculos derivados
    pct_vend = oferta_vendida / oferta_total if oferta_total not in (0, np.nan, None) and pd.notna(oferta_vendida) else np.nan
    
    # Estimación
    v_est = v_mensual if pd.notna(v_mensual) and v_mensual > 0 else v_hist
    estimacion = oferta_act / v_est if pd.notna(v_est) and v_est > 0 and pd.notna(oferta_act) else np.nan

    # 5. Función interna para agregar fila
    def add_row(criterio, prot, precio, m2):
        if pd.isna(precio): return # Si no hay precio (ej. no se encontró prototipo)
        
        rows.append({
            "Desarrollo"                 : proyecto,
            "Desarrollador"              : desarrollador,
            "Criterios"                  : criterio,
            "Constr."                    : m2,
            "Precio final"               : precio,
            "Precio x m2"                : precio / m2 if pd.notna(m2) and m2 > 0 else np.nan,
            "Ventas mensuales históricas": v_hist,
            "Ventas mensuales"           : v_mensual,
            "Oferta disponible anterior" : oferta_ant,
            "Oferta disponible actual"   : oferta_act,
            "Oferta vendida"             : oferta_vendida,
            "Oferta total"               : oferta_total,
            "% vendido"                  : pct_vend,
            "# de meses en venta"        : meses_venta,
            "Estimación"                 : estimacion,
            "Enganche"                   : enganche,
            "Tipo de proyecto"           : tipo,
            "Zona"                       : zona
        })

    # Agregar las 3 líneas
    add_row("+vend", prot_ven, precio_ven, m2_ven)
    add_row("Min",   prot_min, precio_min, m2_min)
    add_row("Max",   prot_max, precio_max, m2_max)

# -------------------------------------------------------------------
# 9. Guardar CSV
# -------------------------------------------------------------------
df_3lineas = pd.DataFrame(rows)
if not df_3lineas.empty:
    df_3lineas['Tipo de proyecto'] = df_3lineas['Tipo de proyecto'].str.capitalize()

df_3lineas.to_csv("Resumen_Disponibles_3_lineas.csv", index=False, encoding="utf-8-sig")

print("Archivo generado: Resumen_Disponibles_3_lineas.csv")
df_3lineas.head(10)

Archivo generado: Resumen_Disponibles_3_lineas.csv


Desarrollo Desarrollador Criterios  \
0                                     5th Level       Privado     +vend   
1                                     5th Level       Privado       Min   
2                                     5th Level       Privado       Max   
3                                         Adora        Lafher     +vend   
4                                         Adora        Lafher       Min   
5                                         Adora        Lafher       Max   
6  Aguamarina Talismán- Torre Aqua Vista Ciudad        Vicasa     +vend   
7  Aguamarina Talismán- Torre Aqua Vista Ciudad        Vicasa       Min   
8  Aguamarina Talismán- Torre Aqua Vista Ciudad        Vicasa       Max   
9  Aguamarina Talismán- Torre Azul Vista al Mar        Vicasa     +vend   

   Constr.  Precio final   Precio x m2  Ventas mensuales históricas  \
0    91.00     2980000.0  32747.252747                     0.333333   
1    91.00     2980000.0  32747.252747                     0.333333   
2    91.00     3340000.0  36703.296703                     0.333333   
3    65.33     2268000.0  34716.056942                     1.812500   
4    65.33     2268000.0  34716.056942                     1.812500   
5    65.33     2268000.0  34716.056942                     1.812500   
6    66.00     4077292.0  61777.151515                     1.133333   
7    66.00     4077292.0  61777.151515                     1.133333   
8    79.00     5151667.0  65210.974684                     1.133333   
9    88.00     5181111.0  58876.261364                     7.644444   

   Ventas mensuales  Oferta disponible anterior  Oferta disponible actual  \
0          0.333333                        16.0                      15.0   
1          0.333333                        16.0                      15.0   
2          0.333333                        16.0                      15.0   
3          0.666667                        20.0                      18.0   
4          0.666667                        20.0                      18.0   
5          0.666667                        20.0                      18.0   
6          0.000000                        25.0                      25.0   
7          0.000000                        25.0                      25.0   
8          0.000000                        25.0                      25.0   
9          0.000000                        28.0                      41.0   

   Oferta vendida  Oferta total  % vendido  # de meses en venta  Estimación  \
0             9.0          24.0   0.375000                   27   45.000000   
1             9.0          24.0   0.375000                   27   45.000000   
2             9.0          24.0   0.375000                   27   45.000000   
3            58.0          76.0   0.763158                   32   27.000000   
4            58.0          76.0   0.763158                   32   27.000000   
5            58.0          76.0   0.763158                   32   27.000000   
6            51.0          76.0   0.671053                   45   22.058824   
7            51.0          76.0   0.671053                   45   22.058824   
8            51.0          76.0   0.671053                   45   22.058824   
9           344.0         385.0   0.893506                   45    5.363372   

  Enganche Tipo de proyecto                Zona  
0      0.3         Vertical    Centro Playa Sur  
1      0.3         Vertical    Centro Playa Sur  
2      0.3         Vertical    Centro Playa Sur  
3      0.1         Vertical      Real del Valle  
4      0.1         Vertical      Real del Valle  
5      0.1         Vertical      Real del Valle  
6     0.15         Vertical      Malecón Ciudad  
7     0.15         Vertical      Malecón Ciudad  
8     0.15         Vertical      Malecón Ciudad  
9     0.15         Vertical  Malecón ocean view

In [ ]:
import pandas as pd
import numpy as np

# -------------------------------------------------------------------
# 1. Ruta del archivo Excel
# -------------------------------------------------------------------
excel_path = r"BD_Mazatlan.xlsm"

# -------------------------------------------------------------------
# 2. Cargar hojas necesarias
# -------------------------------------------------------------------
vertical   = pd.read_excel(excel_path, sheet_name="Vertical")
horizontal = pd.read_excel(excel_path, sheet_name="Horizontal")
lote       = pd.read_excel(excel_path, sheet_name="Lote")

ventas   = pd.read_excel(excel_path, sheet_name="Ventas")
precios  = pd.read_excel(excel_path, sheet_name="Precios")
info_v   = pd.read_excel(excel_path, sheet_name="Info_Prototipos_vertical")
info_h   = pd.read_excel(excel_path, sheet_name="Info_Prototipos_horizontal")
info_l   = pd.read_excel(excel_path, sheet_name="Info_Prototipos_lote")

# -------------------------------------------------------------------
# 3. Helper para saber tipo de proyecto (igual que en 3_lineas)
# -------------------------------------------------------------------
def build_tipo_map():
    m = {}
    for tipo, df in [("vertical", vertical),
                     ("horizontal", horizontal),
                     ("lote", lote)]:
        for dev in df["Nombre_desarrollo"].dropna().unique():
            m[dev] = tipo
    return m

tipo_map = build_tipo_map()

# -------------------------------------------------------------------
# 4. Proyectos objetivo (MISMA LÓGICA que Resumen_Disponibles_3_lineas)
# -------------------------------------------------------------------
def proyectos_disponibles(df):
    return set(
        df.loc[
            df["Estatus_venta"].astype(str).str.lower().eq("disponible"),
            "Nombre_desarrollo"
        ].dropna()
    )

proy_disp = (
    proyectos_disponibles(vertical) |
    proyectos_disponibles(horizontal) |
    proyectos_disponibles(lote)
)

ultima_fecha_ventas = ventas["Fecha"].max()

def proyectos_vendidos_ultimo_periodo(df):
    mask = (
        df["Estatus_venta"].astype(str).str.lower().eq("vendido")
        & (pd.to_datetime(df["Fecha_fin_ventas"]) == ultima_fecha_ventas)
    )
    return set(df.loc[mask, "Nombre_desarrollo"].dropna())

proy_vendidos = (
    proyectos_vendidos_ultimo_periodo(vertical) |
    proyectos_vendidos_ultimo_periodo(horizontal) |
    proyectos_vendidos_ultimo_periodo(lote)
)

proyectos_objetivo = sorted(proy_disp | proy_vendidos)

# -------------------------------------------------------------------
# 5. Normalizar tipo en minúsculas en Ventas y Precios
# -------------------------------------------------------------------
ventas["tipo_lower"]  = ventas["Tipo_proyecto"].astype(str).str.strip().str.lower()
precios["tipo_lower"] = precios["Tipo_proyecto"].astype(str).str.strip().str.lower()

# -------------------------------------------------------------------
# 6. Utilidad para convertir a número seguro
# -------------------------------------------------------------------
def to_float(x):
    try:
        if pd.isna(x):
            return np.nan
        return float(str(x).replace(",", "").strip())
    except:
        return np.nan

# -------------------------------------------------------------------
# 7. Meta de proyectos: Desarrolladora, Zona, Meses_venta, Fecha_inicio_venta, Oferta_total
# -------------------------------------------------------------------
def build_proyectos_meta():
    frames = []

    v = vertical.copy()
    v["tipo_lower"] = "vertical"
    v = v.assign(
        Oferta_total=v.get("Departamentos_planeados", np.nan)
    )
    frames.append(
        v[["Nombre_desarrollo", "tipo_lower", "Desarrolladora", "Zona",
           "Meses_venta", "Fecha_inicio_venta", "Oferta_total"]]
    )

    h = horizontal.copy()
    h["tipo_lower"] = "horizontal"
    h = h.assign(
        Oferta_total=h.get("Casas_planeados", np.nan)
    )
    frames.append(
        h[["Nombre_desarrollo", "tipo_lower", "Desarrolladora", "Zona",
           "Meses_venta", "Fecha_inicio_venta", "Oferta_total"]]
    )

    l = lote.copy()
    l["tipo_lower"] = "lote"
    l = l.assign(
        Oferta_total=l.get("Lotes_planeados", np.nan)
    )
    frames.append(
        l[["Nombre_desarrollo", "tipo_lower", "Desarrolladora", "Zona",
           "Meses_venta", "Fecha_inicio_venta", "Oferta_total"]]
    )

    meta = pd.concat(frames, ignore_index=True)
    meta = meta.drop_duplicates(subset=["Nombre_desarrollo", "tipo_lower"])
    return meta

proyectos_meta = build_proyectos_meta()

# -------------------------------------------------------------------
# 8. Índice de prototipos (m2, recámaras, baños, etc.)
# -------------------------------------------------------------------
def build_info_proto():
    frames = []

    v = info_v.copy()
    v["tipo_lower"] = "vertical"
    frames.append(v)

    h = info_h.copy()
    h["tipo_lower"] = "horizontal"
    frames.append(h)

    l = info_l.copy()
    l["tipo_lower"] = "lote"
    frames.append(l)

    info = pd.concat(frames, ignore_index=True)
    return info

info_proto = build_info_proto()

# -------------------------------------------------------------------
# 9. Métricas de ventas por proyecto (dev + tipo_lower)
# -------------------------------------------------------------------
def get_ventas_metrics_dev(desarrollo, tipo_lower, meses_venta, fecha_inicio_venta):
    """
    Devuelve:
    - v_hist: Ventas_hist = Ventas_acumuladas_último / Meses_venta
    - v_mensual: ritmo del último periodo (para EstMesesV)
    - ventaAgo25: ritmo del penúltimo periodo = Ventas_periodo_penúltimo / meses_entre
    - oferta_actual: Inventario_disponible último
    - vend_acum: Ventas_acumuladas último
    """
    dfv = ventas[
        (ventas["Nombre_desarrollo"] == desarrollo) &
        (ventas["tipo_lower"] == tipo_lower)
    ].sort_values("Fecha").copy()

    if dfv.empty:
        return np.nan, np.nan, np.nan, np.nan, np.nan

    # Asegurar numérico
    for col in ["Ventas_acumuladas", "Ventas_periodo", "Inventario_disponible"]:
        if col in dfv.columns:
            dfv[col] = pd.to_numeric(dfv[col], errors="coerce")

    last = dfv.iloc[-1]
    last_date = pd.to_datetime(last["Fecha"])

    ventas_acum_last = to_float(last.get("Ventas_acumuladas", np.nan))
    inv_last         = to_float(last.get("Inventario_disponible", np.nan))

    # Meses_venta numérico
    meses_venta_num = to_float(meses_venta)

    # Ventas históricas
    if pd.notna(ventas_acum_last) and pd.notna(meses_venta_num) and meses_venta_num != 0:
        v_hist = ventas_acum_last / meses_venta_num
    else:
        v_hist = np.nan

    v_mensual  = np.nan
    ventaAgo25 = np.nan

    if len(dfv) >= 2:
        prev = dfv.iloc[-2]
        prev_date = pd.to_datetime(prev["Fecha"])

        diff_meses = (last_date.year - prev_date.year) * 12 + (last_date.month - prev_date.month)
        if diff_meses <= 0:
            diff_meses = 1

        ventas_periodo_last = to_float(last.get("Ventas_periodo", np.nan))
        ventas_periodo_prev = to_float(prev.get("Ventas_periodo", np.nan))

        # Ritmo último periodo (v_mensual)
        if pd.notna(ventas_periodo_last):
            v_mensual = ventas_periodo_last / diff_meses

        # VentaAgo25 = ritmo del penúltimo periodo
        if pd.notna(ventas_periodo_prev):
            ventaAgo25 = ventas_periodo_prev / diff_meses
    else:
        # Solo un registro de ventas
        fecha_ini = pd.to_datetime(fecha_inicio_venta) if pd.notna(fecha_inicio_venta) else None
        if fecha_ini is not None:
            mismo_mes_anyo = (fecha_ini.year == last_date.year) and (fecha_ini.month == last_date.month)
            if mismo_mes_anyo:
                # Empezó en este periodo: usar ventas_acumuladas como ritmo inicial
                v_mensual = ventas_acum_last
            else:
                # Ya venía de antes, usar histórico
                v_mensual = v_hist
        else:
            v_mensual = v_hist

        ventaAgo25 = np.nan  # no hay penúltimo

    return v_hist, v_mensual, ventaAgo25, inv_last, ventas_acum_last

# -------------------------------------------------------------------
# 10. Prototipo más vendido (último periodo de PRECIOS)
# -------------------------------------------------------------------
def get_prototipo_mas_vendido_ultimo(df_last):
    """
    df_last: precios de un desarrollo+tipo en la ÚLTIMA FECHA, Precio > 0.
    Prioridad:
    1) marcado " + ven" = VERDADERO/TRUE/SI/1
    2) de lo contrario, prototipo con menor precio > 0
    """
    prot_mas_vendido = None

    if " + ven" in df_last.columns:
        col = df_last[" + ven"].astype(str).str.strip().str.upper()
        mask_true = col.isin(["VERDADERO", "TRUE", "SÍ", "SI", "1", "YES"])
        df_mark = df_last[mask_true]
        if not df_mark.empty:
            prot_mas_vendido = df_mark.iloc[0]["Nombre_prototipos"]

    if prot_mas_vendido is None and not df_last.empty:
        row_min = df_last.loc[df_last["Precio"].idxmin()]
        prot_mas_vendido = row_min["Nombre_prototipos"]

    return prot_mas_vendido

# -------------------------------------------------------------------
# 11. Construir reporte por prototipo SOLO para proyectos_objetivo
# -------------------------------------------------------------------
rows = []

for dev in proyectos_objetivo:

    tipo_lower = tipo_map.get(dev)
    if tipo_lower is None:
        continue

    # Meta del proyecto
    meta_row = proyectos_meta[
        (proyectos_meta["Nombre_desarrollo"] == dev) &
        (proyectos_meta["tipo_lower"] == tipo_lower)
    ]

    if meta_row.empty:
        continue

    meta_row = meta_row.iloc[0]
    desarrolladora   = meta_row.get("Desarrolladora", np.nan)
    zona             = meta_row.get("Zona", np.nan)
    meses_venta      = meta_row.get("Meses_venta", np.nan)
    fecha_inicio_ven = meta_row.get("Fecha_inicio_venta", np.nan)
    oferta_total     = to_float(meta_row.get("Oferta_total", np.nan))

    # Métricas de ventas
    v_hist, v_mensual, ventaAgo25, oferta_actual, vend_acum = get_ventas_metrics_dev(
        desarrollo=dev,
        tipo_lower=tipo_lower,
        meses_venta=meses_venta,
        fecha_inicio_venta=fecha_inicio_ven
    )

    # % vendido
    if pd.notna(oferta_total) and oferta_total != 0 and pd.notna(vend_acum):
        pct_vendido = vend_acum / oferta_total
    else:
        pct_vendido = np.nan

    # EstMesesV = Estimación = inventario actual / (v_mensual si >0, si no v_hist)
    if pd.notna(v_mensual) and v_mensual > 0:
        v_est = v_mensual
    else:
        v_est = v_hist

    if pd.notna(oferta_actual) and pd.notna(v_est) and v_est != 0:
        est_meses = oferta_actual / v_est
    else:
        est_meses = np.nan

    # PRECIOS: solo último periodo por dev+tipo
    df_prec_dev = precios[
        (precios["Nombre_desarrollo"] == dev) &
        (precios["tipo_lower"] == tipo_lower)
    ].copy()

    df_prec_dev["Fecha"] = pd.to_datetime(df_prec_dev["Fecha"])
    df_prec_dev["Precio"] = pd.to_numeric(df_prec_dev["Precio"], errors="coerce")

    fechas = sorted(df_prec_dev["Fecha"].dropna().unique())
    if len(fechas) == 0:
        continue

    last_date = fechas[-1]

    df_last = df_prec_dev[
        (df_prec_dev["Fecha"] == last_date) &
        (df_prec_dev["Precio"] > 0)
    ].copy()

    if df_last.empty:
        continue

    # Prototipo más vendido (definido solo en el ÚLTIMO periodo)
    prot_mas_vendido = get_prototipo_mas_vendido_ultimo(df_last)

    # Info detallada de prototipos (m2, recámaras, baños)
    info_dev = info_proto[
        (info_proto["Nombre_desarrollo"] == dev) &
        (info_proto["tipo_lower"] == tipo_lower)
    ]

    # Etiqueta Tipo
    tipo_label = {
        "vertical": "Vertical",
        "horizontal": "Horizontal",
        "lote": "Lote"
    }.get(tipo_lower, tipo_lower.capitalize())

    # Una fila por prototipo con datos ÚLTIMO periodo
    for _, rp in df_last.iterrows():
        prot   = rp["Nombre_prototipos"]
        precio = to_float(rp["Precio"])

        # Info del prototipo
        info_row = info_dev[info_dev["Nombre_prototipos"] == prot]
        if not info_row.empty:
            info_row = info_row.iloc[0]
            m2_cons = to_float(info_row.get("Medida_construcción", np.nan))
            m2_terr = to_float(info_row.get("Medida_terreno", np.nan))
            rec     = to_float(info_row.get("Número_recámaras", np.nan))
            banos   = to_float(info_row.get("Baños_completos", np.nan))
            medios  = to_float(info_row.get("Medios_baños", np.nan))
        else:
            m2_cons = m2_terr = rec = banos = medios = np.nan

        pxm2_cons = precio / m2_cons if pd.notna(precio) and pd.notna(m2_cons) and m2_cons != 0 else np.nan
        pxm2_terr = precio / m2_terr if pd.notna(precio) and pd.notna(m2_terr) and m2_terr != 0 else np.nan

        es_mas_vendido = (
            isinstance(prot_mas_vendido, str)
            and isinstance(prot, str)
            and prot.strip().lower() == prot_mas_vendido.strip().lower()
        )
        mas_vendido_flag = "+ven" if es_mas_vendido else ""

        rows.append({
            "Nombre_desarrollo"          : dev,
            "Desarrolladora"             : desarrolladora,
            "Nombre_prototipos"          : prot,
            "Precios_vivienda_Julio_2024": precio,          # del ÚLTIMO periodo
            "Medida_construcción"        : m2_cons,
            "Medida_terreno"             : m2_terr,
            "precio xm2 construccion"    : pxm2_cons,
            "precio xm2 terreno"         : pxm2_terr,
            "Número_recámaras"           : rec,
            "Baños_completos"            : banos,
            "Medios_baños"               : medios,
            "Ventas_hist"                : v_hist,
            "VentaAgo25"                 : ventaAgo25,
            "Oferta disponible actual"   : oferta_actual,
            "% vendido"                  : pct_vendido,
            "EstMesesV"                  : est_meses,
            "Zona"                       : zona,
            "Más vendido"                : mas_vendido_flag,
            "Tipo"                       : tipo_label
        })

# -------------------------------------------------------------------
# 12. Crear DataFrame y guardar CSV
# -------------------------------------------------------------------
df_reporte_prot = pd.DataFrame(rows)

output_csv = "Reporte_prototipos.csv"
df_reporte_prot.to_csv(output_csv, index=False, encoding="utf-8-sig")

print(f"Archivo generado: {output_csv}")
df_reporte_prot.head(20)


In [ ]:
import pandas as pd
import numpy as np
import unicodedata
import re
from IPython.display import display

# ==========================================================
# 1. Funciones helper
# ==========================================================
def to_float(x):
    try:
        if pd.isna(x):
            return np.nan
        return float(str(x).replace("$", "").replace(",", "").strip())
    except:
        return np.nan

def normalizar_nombre(x):
    """Normaliza nombre de proyecto para empatar entre archivos."""
    if pd.isna(x):
        return ""
    x = str(x)
    # quitar acentos
    x = ''.join(
        c for c in unicodedata.normalize('NFD', x)
        if unicodedata.category(c) != 'Mn'
    )
    # minúsculas
    x = x.lower()
    # colapsar múltiples espacios
    x = re.sub(r"\s+", " ", x)
    # quitar espacios alrededor de guiones
    x = x.replace(" -", "-").replace("- ", "-")
    # strip
    x = x.strip()
    return x

def num_equal(a, b, tol=1e-6):
    """Igualdad numérica con tolerancia, considerando NaNs."""
    return np.isclose(a, b, atol=tol) | (pd.isna(a) & pd.isna(b))

# ==========================================================
# 2. Cargar CSVs
# ==========================================================
df1 = pd.read_csv("Resumen_Disponibles_1_linea.csv")
df3 = pd.read_csv("Resumen_Disponibles_3_lineas.csv")
dfp = pd.read_csv("Reporte_prototipos.csv")

# Detectar nombre de columna   +vend en df1
if " +vend" in df1.columns:
    col_plus_1 = " +vend"
elif  "  +ven" in df1.columns:
    col_plus_1 =  "  +ven"
else:
    raise ValueError("No encontré la columna '+ven' en Resumen_Disponibles_1_linea.csv")

# Detectar nombre de columna de precios en Reporte_prototipos
if "Precios_vivienda_Julio_2025" in dfp.columns:
    col_prec_prot = "Precios_vivienda_Julio_2025"
elif "Precios_vivienda_Julio_2024" in dfp.columns:
    col_prec_prot = "Precios_vivienda_Julio_2024"
else:
    raise ValueError("No encontré 'Precios_vivienda_Julio_2025' ni 'Precios_vivienda_Julio_2024' en Reporte_prototipos.csv")

# ==========================================================
# 3. Normalizar nombres de desarrollo
# ==========================================================
df1["dev_norm"] = df1["Desarrollo"].apply(normalizar_nombre)
df3["dev_norm"] = df3["Desarrollo"].apply(normalizar_nombre)
dfp["dev_norm"] = dfp["Nombre_desarrollo"].apply(normalizar_nombre)

# ==========================================================
# 4. Normalizar columnas numéricas clave
# ==========================================================
num_like_cols_1 = [
    col_plus_1, "Precio mínimo", "Precio máximo",
    "Ventas mensuales históricas", "Ventas mensuales",
    "Oferta disponible actual", "% vendido"
]

num_like_cols_3 = [
    "Precio final", "Ventas mensuales históricas", "Ventas mensuales",
    "Oferta disponible actual", "% vendido"
]

num_like_cols_p = [
    col_prec_prot, "Ventas_hist", "VentaAgo25",
    "Oferta disponible actual", "% vendido"
]

for col in num_like_cols_1:
    if col in df1.columns:
        df1[col] = df1[col].apply(to_float)

for col in num_like_cols_3:
    if col in df3.columns:
        df3[col] = df3[col].apply(to_float)

for col in num_like_cols_p:
    if col in dfp.columns:
        dfp[col] = dfp[col].apply(to_float)

# ==========================================================
# 5. Validar número y lista de proyectos únicos
# ==========================================================
proy_1 = set(df1["dev_norm"].unique())
proy_3 = set(df3["dev_norm"].unique())
proy_p = set(dfp["dev_norm"].unique())

print("Proyectos únicos en Resumen_Disponibles_1_linea   :", len(proy_1))
print("Proyectos únicos en Resumen_Disponibles_3_lineas  :", len(proy_3))
print("Proyectos únicos en Reporte_prototipos            :", len(proy_p))

print("\nDiferencias de proyectos (usando dev_norm):")
print("- En 1_linea pero NO en 3_lineas:", proy_1 - proy_3)
print("- En 3_lineas pero NO en 1_linea:", proy_3 - proy_1)
print("- En 1_linea pero NO en prototipos:", proy_1 - proy_p)
print("- En prototipos pero NO en 1_linea:", proy_p - proy_1)

# ==========================================================
# 6. Construir vista agregada de 3_lineas por proyecto
#    (+vend, Min, Max y variables comunes)
# ==========================================================
df3_plus = df3[df3["Criterios"].astype(str).str.strip().str.lower().eq( "  +ven")].copy()
df3_min  = df3[df3["Criterios"].astype(str).str.strip().str.lower().eq("min")].copy()
df3_max  = df3[df3["Criterios"].astype(str).str.strip().str.lower().eq("max")].copy()

df3_plus = df3_plus.rename(columns={"Precio final": "Precio_ven_3"})[
    ["dev_norm", "Desarrollo", "Precio_ven_3"]
]
df3_min  = df3_min.rename(columns={"Precio final": "Precio_min_3"})[
    ["dev_norm", "Precio_min_3"]
]
df3_max  = df3_max.rename(columns={"Precio final": "Precio_max_3"})[
    ["dev_norm", "Precio_max_3"]
]

# Base de variables comunes de 3_lineas (una fila por dev_norm)
df3_base = df3.sort_values("Desarrollo").groupby("dev_norm", as_index=False).first()

cols_map_3 = {
    "Zona": "Zona_3",
    "Ventas mensuales históricas": "VHist_3",
    "Ventas mensuales": "VMens_3",
    "Tipo de proyecto": "Tipo_3",
    "Oferta disponible actual": "OfertaAct_3",
    "Desarrollador": "Desarrollador_3",
    "% vendido": "PctVend_3",
}

df3_base = df3_base[["dev_norm"] + list(cols_map_3.keys())].rename(columns=cols_map_3)

# Unimos todo lo de 3_lineas
df3_agg = df3_base.merge(df3_plus[["dev_norm", "Precio_ven_3"]], on="dev_norm", how="left") \
                  .merge(df3_min, on="dev_norm", how="left") \
                  .merge(df3_max, on="dev_norm", how="left")

# ==========================================================
# 7. Construir vista agregada de Reporte_prototipos
# ==========================================================
# Base con variables comunes (una fila por dev_norm)
dfp_base = dfp.sort_values("Nombre_desarrollo").groupby("dev_norm", as_index=False).first()

cols_map_p = {
    "Zona": "Zona_p",
    "Ventas_hist": "VHist_p",
    "VentaAgo25": "VMens_p",
    "Tipo": "Tipo_p",
    "Oferta disponible actual": "OfertaAct_p",
    "Desarrolladora": "Desarrollador_p",
    "% vendido": "PctVend_p",
    "Nombre_desarrollo": "Nombre_desarrollo_p"
}
cols_keep_p = ["dev_norm"] + list(cols_map_p.keys())
dfp_base = dfp_base[cols_keep_p].rename(columns=cols_map_p)

# Min y max de precios por proyecto desde Reporte_prototipos
dfp_agg_prec = dfp.groupby("dev_norm")[col_prec_prot].agg(["min", "max"]).reset_index()
dfp_agg_prec = dfp_agg_prec.rename(columns={
    "min": "Precio_min_prot",
    "max": "Precio_max_prot"
})

# Merge base + min/max
dfp_agg = dfp_base.merge(dfp_agg_prec, on="dev_norm", how="left")

# ==========================================================
# 8. Merge maestro: df1 + df3_agg + dfp_agg
# ==========================================================
val = df1.merge(df3_agg, on="dev_norm", how="left") \
         .merge(dfp_agg, on="dev_norm", how="left")

print("\nFilas en tabla de validación (val):", len(val))

# ==========================================================
# 9. Validar +ven, Precio mínimo y máximo (1_linea vs 3_lineas)
# ==========================================================
val["ok_ven_1_vs_3"] = num_equal(val[col_plus_1], val["Precio_ven_3"], tol=1)
val["ok_min_1_vs_3"] = num_equal(val["Precio mínimo"], val["Precio_min_3"], tol=1)
val["ok_max_1_vs_3"] = num_equal(val["Precio máximo"], val["Precio_max_3"], tol=1)

print("\n--- Proyectos donde +ven NO coincide entre 1_linea y 3_lineas ---")
display(val[~val["ok_ven_1_vs_3"]][["Desarrollo", col_plus_1, "Precio_ven_3"]])

print("\n--- Proyectos donde Precio mínimo NO coincide entre 1_linea y 3_lineas ---")
display(val[~val["ok_min_1_vs_3"]][["Desarrollo", "Precio mínimo", "Precio_min_3"]])

print("\n--- Proyectos donde Precio máximo NO coincide entre 1_linea y 3_lineas ---")
display(val[~val["ok_max_1_vs_3"]][["Desarrollo", "Precio máximo", "Precio_max_3"]])

# ==========================================================
# 10. Validar variables cruzadas 1_linea vs 3_lineas vs prototipos
# ==========================================================
# Zona
val["ok_zona_1_3"] = val["Zona"] == val["Zona_3"]
val["ok_zona_1_p"] = val["Zona"] == val["Zona_p"]

# Ventas mensuales históricas
val["ok_vhist_1_3"] = num_equal(val["Ventas mensuales históricas"], val["VHist_3"])
val["ok_vhist_1_p"] = num_equal(val["Ventas mensuales históricas"], val["VHist_p"])

# Ventas mensuales / VentaAgo25
val["ok_vmens_1_3"] = num_equal(val["Ventas mensuales"], val["VMens_3"])
val["ok_vmens_1_p"] = num_equal(val["Ventas mensuales"], val["VMens_p"])

# Tipo de proyecto
val["ok_tipo_1_3"] = val["Tipo de proyecto"] == val["Tipo_3"]
val["ok_tipo_1_p"] = val["Tipo de proyecto"].astype(str).str.strip().str.lower() == \
                     val["Tipo_p"].astype(str).str.strip().str.lower()

# Oferta disponible actual
val["ok_oferta_1_3"] = num_equal(val["Oferta disponible actual"], val["OfertaAct_3"])
val["ok_oferta_1_p"] = num_equal(val["Oferta disponible actual"], val["OfertaAct_p"])

# Desarrollador
val["ok_desarr_1_3"] = val["Desarrollador"] == val["Desarrollador_3"]
val["ok_desarr_1_p"] = val["Desarrollador"] == val["Desarrollador_p"]

# % vendido
val["ok_pct_1_3"] = num_equal(val["% vendido"], val["PctVend_3"])
val["ok_pct_1_p"] = num_equal(val["% vendido"], val["PctVend_p"])

print("\n--- Mismatches de Zona (1 vs 3 y 1 vs prototipos) ---")
display(val[~val["ok_zona_1_3"]][["Desarrollo","Zona","Zona_3"]])
display(val[~val["ok_zona_1_p"]][["Desarrollo","Zona","Zona_p"]])

print("\n--- Mismatches de Ventas mensuales históricas ---")
display(val[~(val["ok_vhist_1_3"] & val["ok_vhist_1_p"])][
    ["Desarrollo","Ventas mensuales históricas","VHist_3","VHist_p"]
])

print("\n--- Mismatches de Ventas mensuales / VentaAgo25 ---")
display(val[~(val["ok_vmens_1_3"] & val["ok_vmens_1_p"])][
    ["Desarrollo","Ventas mensuales","VMens_3","VMens_p"]
])

print("\n--- Mismatches de Tipo de proyecto ---")
display(val[~(val["ok_tipo_1_3"] & val["ok_tipo_1_p"])][
    ["Desarrollo","Tipo de proyecto","Tipo_3","Tipo_p"]
])

print("\n--- Mismatches de Oferta disponible actual ---")
display(val[~(val["ok_oferta_1_3"] & val["ok_oferta_1_p"])][
    ["Desarrollo","Oferta disponible actual","OfertaAct_3","OfertaAct_p"]
])

print("\n--- Mismatches de Desarrollador ---")
display(val[~(val["ok_desarr_1_3"] & val["ok_desarr_1_p"])][
    ["Desarrollo","Desarrollador","Desarrollador_3","Desarrollador_p"]
])

print("\n--- Mismatches de % vendido ---")
display(val[~(val["ok_pct_1_3"] & val["ok_pct_1_p"])][
    ["Desarrollo","% vendido","PctVend_3","PctVend_p"]
])

# ==========================================================
# 11. Validar min y max de precios por prototipo vs Resúmenes
# ==========================================================
val["ok_pmin_1_vs_prot"] = num_equal(val["Precio mínimo"], val["Precio_min_prot"], tol=1)
val["ok_pmax_1_vs_prot"] = num_equal(val["Precio máximo"], val["Precio_max_prot"], tol=1)

print("\n--- Proyectos donde Precio mínimo NO coincide con prototipos ---")
display(val[~val["ok_pmin_1_vs_prot"]][
    ["Desarrollo","Precio mínimo","Precio_min_3","Precio_min_prot"]
])

print("\n--- Proyectos donde Precio máximo NO coincide con prototipos ---")
display(val[~val["ok_pmax_1_vs_prot"]][
    ["Desarrollo","Precio máximo","Precio_max_3","Precio_max_prot"]
])

# ==========================================================
# 12. Resumen global
# ==========================================================
print("\n================= RESUMEN GLOBAL =================")
print("¿Misma lista de proyectos en 1_linea y 3_lineas?   :", proy_1 == proy_3)
print("¿Misma lista de proyectos en 1_linea y prototipos?:", proy_1 == proy_p)

print("\nProporción de coincidencias (≈1.0 es perfecto):")
print(" +ven  1 vs 3_lineas          :", val["ok_ven_1_vs_3"].mean())
print(" Precio min 1 vs 3_lineas     :", val["ok_min_1_vs_3"].mean())
print(" Precio max 1 vs 3_lineas     :", val["ok_max_1_vs_3"].mean())
print(" Zona 1 vs 3 & prototipos     :", (val["ok_zona_1_3"] & val["ok_zona_1_p"]).mean())
print(" Ventas hist 1 vs 3 & prot    :", (val["ok_vhist_1_3"] & val["ok_vhist_1_p"]).mean())
print(" Ventas mens 1 vs 3 & prot    :", (val["ok_vmens_1_3"] & val["ok_vmens_1_p"]).mean())
print(" Tipo 1 vs 3 & prot           :", (val["ok_tipo_1_3"] & val["ok_tipo_1_p"]).mean())
print(" Oferta act 1 vs 3 & prot     :", (val["ok_oferta_1_3"] & val["ok_oferta_1_p"]).mean())
print(" Desarrollador 1 vs 3 & prot  :", (val["ok_desarr_1_3"] & val["ok_desarr_1_p"]).mean())
print(" % vendido 1 vs 3 & prot      :", (val["ok_pct_1_3"] & val["ok_pct_1_p"]).mean())
print(" Precio min 1 vs prot         :", val["ok_pmin_1_vs_prot"].mean())
print(" Precio max 1 vs prot         :", val["ok_pmax_1_vs_prot"].mean())
print("==================================================")


Proyectos únicos en Resumen_Disponibles_1_linea   : 204
Proyectos únicos en Resumen_Disponibles_3_lineas  : 204
Proyectos únicos en Reporte_prototipos            : 204

Diferencias de proyectos (usando dev_norm):
- En 1_linea pero NO en 3_lineas: set()
- En 3_lineas pero NO en 1_linea: set()
- En 1_linea pero NO en prototipos: set()
- En prototipos pero NO en 1_linea: set()

Filas en tabla de validación (val): 204

--- Proyectos donde +ven NO coincide entre 1_linea y 3_lineas ---


Desarrollo       +vend  Precio_ven_3
22             Bio Towers  2630000.00           0.0
98   Maraká Living Condos  4976650.26           0.0
109   Meraki Departmentos  3300000.00           0.0
150  Rivera Departamentos  2975000.00           0.0
166      The O Residences  3725000.00           0.0
180          Torres Navia  2900000.00           0.0
182      Un Modern Living  3235000.00           0.0


--- Proyectos donde Precio mínimo NO coincide entre 1_linea y 3_lineas ---


Empty DataFrame
Columns: [Desarrollo, Precio mínimo, Precio_min_3]
Index: []


--- Proyectos donde Precio máximo NO coincide entre 1_linea y 3_lineas ---


...


--- Proyectos donde Precio mínimo NO coincide con prototipos ---


Empty DataFrame
Columns: [Desarrollo, Precio mínimo, Precio_min_3, Precio_min_prot]
Index: []


--- Proyectos donde Precio máximo NO coincide con prototipos ---


Empty DataFrame
Columns: [Desarrollo, Precio máximo, Precio_max_3, Precio_max_prot]
Index: []


================= RESUMEN GLOBAL =================
¿Misma lista de proyectos en 1_linea y 3_lineas?   : True
¿Misma lista de proyectos en 1_linea y prototipos?: True

Proporción de coincidencias (≈1.0 es perfecto):
 +ven  1 vs 3_lineas          : 0.9656862745098039
 Precio min 1 vs 3_lineas     : 1.0
 Precio max 1 vs 3_lineas     : 1.0
 Zona 1 vs 3 & prototipos     : 0.9852941176470589
 Ventas hist 1 vs 3 & prot    : 0.03431372549019608
 Ventas mens 1 vs 3 & prot    : 0.10784313725490197
 Tipo 1 vs 3 & prot           : 1.0
 Oferta act 1 vs 3 & prot     : 0.9901960784313726
 Desarrollador 1 vs 3 & prot  : 0.9803921568627451
 % vendido 1 vs 3 & prot      : 0.0
 Precio min 1 vs prot         : 1.0
 Precio max 1 vs prot         : 1.0


In [1]:
import pandas as pd
import numpy as np

# -------------------------------------------------------------------
# 1. Ruta del archivo Excel
# -------------------------------------------------------------------
excel_path = r"C:\Users\julio\OneDrive\Documentos\Trabajo\Ideas Frescas\Proyectos\REM\BD\BD_Mazatlan.xlsm"


ventas   = pd.read_excel(excel_path, sheet_name="Ventas")


In [2]:
ventas

Fecha     Nombre_desarrollo Tipo_proyecto  Ventas_acumuladas  \
0    2023-10-01             5th Level      Vertical                5.0   
1    2024-01-01             5th Level      Vertical                6.0   
2    2024-04-01             5th Level      Vertical                6.0   
3    2024-07-01             5th Level      Vertical                7.0   
4    2024-10-01             5th Level      Vertical                6.0   
...         ...                   ...           ...                ...   
3513 2025-10-01            Zúñiga 601      Vertical               11.0   
3514 2021-07-01  Zyanya Departamentos      Vertical                8.0   
3515 2021-11-01  Zyanya Departamentos      Vertical                9.0   
3516 2022-03-01  Zyanya Departamentos      Vertical               14.0   
3517 2022-07-01  Zyanya Departamentos      Vertical               16.0   

      Ventas_periodo  Inventario_disponible  Numero_de_viviendas_planeadas  \
0                5.0                   19.0                           24.0   
1                1.0                   18.0                           24.0   
2                0.0                   18.0                           24.0   
3                1.0                   17.0                           24.0   
4                0.0                   18.0                           24.0   
...              ...                    ...                            ...   
3513             0.0                    1.0                           12.0   
3514             8.0                    8.0                           16.0   
3515             1.0                    7.0                           16.0   
3516             5.0                    2.0                           16.0   
3517             2.0                    0.0                           16.0   

     Nota  Ventas_detenidas  
0     NaN               0.0  
1     NaN               0.0  
2     NaN               0.0  
3     NaN               0.0  
4     NaN               0.0  
...   ...               ...  
3513  NaN               0.0  
3514  NaN               0.0  
3515  NaN               0.0  
3516  NaN               0.0  
3517  NaN               0.0  

[3518 rows x 9 columns]

In [3]:
ventas['Ventas_detenidas'].value_counts()

Ventas_detenidas
0.0    3273
1.0     244
Name: count, dtype: int64